In [1]:
import os
os.chdir('../')

In [2]:
%pwd

'c:\\mlops projects\\text-summarization'

In [3]:
from dataclasses import dataclass
from pathlib import Path
@dataclass(frozen=True)
class DataIngestionConfig:
    root_dir : Path
    source_URL : str
    local_data_file : Path
    unzip_dir : Path

In [4]:
from textsummarizer.constants import *
from textsummarizer.utils.common import read_yaml, create_directories


class ConfigurationManager:
    def __init__(
        self,
        config_filepath = CONFIG_FILE_PATH,
        params_filepath = PARAMS_FILE_PATH):

        self.config = read_yaml(config_filepath)
        self.params = read_yaml(params_filepath)

        create_directories([self.config.artifacts_root])

    

    def get_data_ingestion_config(self) -> DataIngestionConfig:
        config = self.config.data_ingestion

        create_directories([config.root_dir])

        data_ingestion_config = DataIngestionConfig(
            root_dir=config.root_dir,
            source_URL=config.source_URL,
            local_data_file=config.local_data_file,
            unzip_dir=config.unzip_dir 
        )

        return data_ingestion_config
        

In [5]:
import os
import urllib.request as request
import zipfile
from textsummarizer.logging import logger
from textsummarizer.utils.common import get_size

In [8]:
class DataIngestion:
    def __init__(self, config: DataIngestionConfig):
        self.config = config
        
        
    def download_file(self):
        if not os.path.exists(self.config.local_data_file):
            filename, header = request.urlretrieve(
                url=self.config.source_URL,
                filename = self.config.local_data_file
            )
            logger.info(f'{filename} download! with following info: \n{header}')
            
        else:
            logger.info(f"File already exist size {get_size(Path(self.config.local_data_file))}")
            
            
        
            
            
    def extract_zip_file(self):
        """
        zip_file_path: str
        Extracts the zip file into the data directory
        Function returns None
        """
        unzip_path = self.config.unzip_dir
        os.makedirs(unzip_path, exist_ok=True)
        with zipfile.ZipFile(self.config.local_data_file, 'r') as zip_ref:
            zip_ref.extractall(unzip_path)
            
            
                    
        

In [10]:
try:
    config = ConfigurationManager()
    data_ingestion_config = config.get_data_ingestion_config()
    data_ingestion = DataIngestion(config=data_ingestion_config)
    data_ingestion.download_file()
    data_ingestion.extract_zip_file()
except Exception as e:
    raise e

[2024-08-11 15:50:51,008: INFO: common: yaml file: config\config.yaml loaded successfully]
[2024-08-11 15:50:51,011: INFO: common: yaml file: params.yaml loaded successfully]
[2024-08-11 15:50:51,012: INFO: common: created directory at: artifacts]
[2024-08-11 15:50:51,014: INFO: common: created directory at: artifacts/data_ingestion]
[2024-08-11 15:50:51,016: INFO: 4172299431: File already exist size ~ 7718 KB]
